<a href="https://colab.research.google.com/github/mathilde-lemener/Defi-IA/blob/master/resNet50.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
# -*- coding: utf-8 -*-

# La j'importe plein de trucs qui sont peut etre pas tous très utiles

# Utils
import sys
import os
import shutil
import time
import pickle
import numpy as np

# Deep Learning Librairies
import tensorflow as tf
import keras.preprocessing.image as kpi
import keras.layers as kl
import keras.optimizers as ko
import keras.backend as k
import keras.models as km
import keras.applications as ka

# Visualisaiton des données
from matplotlib import pyplot as plt

In [0]:
# Ici j'indique que je vais utiliser les fichiers qui sont dans google drive, pour ça il va falloir
# cliquer sur le lien indiqué et ecrire dans google colab un code
from google.colab import drive
drive.mount('/content/drive')

# ensuite on demande de dézziper notre fichier (enregistré dans google drive)
!unzip '/content/drive/My Drive/data_airbus_defi.zip'

# ici je créé la liste des fichiers tests pour avoir tous les noms (281.jpg par ex)
from os import listdir
from os.path import isfile, join
fichiers = [f for f in listdir("data_airbus_defi/test") if isfile(join("data_airbus_defi/test", f))]



Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive
Archive:  /content/drive/My Drive/data_airbus_defi.zip
   creating: data_airbus_defi/
  inflating: data_airbus_defi/.DS_Store  
   creating: __MACOSX/
   creating: __MACOSX/data_airbus_defi/
  inflating: __MACOSX/data_airbus_defi/._.DS_Store  
  inflating: data_airbus_defi/template_answer.csv  
   creating: data_airbus_defi/test/
  inflating: data_airbus_defi/test/0.jpg  
  inflating: data_airbus_defi/test/1.jpg  
  inflating: data_airbus_defi/test/10.jpg  
  

In [0]:
# ICI Je créé un modele
#Import
from keras.applications.resnet50 import ResNet50
from keras.preprocessing import image
from keras.models import Model, Sequential
from keras.layers import Dense, GlobalAveragePooling2D, Dropout, Flatten
from keras import backend as K
from keras.applications.resnet50 import preprocess_input
from keras import regularizers
from keras.callbacks import EarlyStopping


#base_model = ResNet50(weights="imagenet", include_top=False)
base_model = ResNet50(weights="imagenet", input_shape=(128,128,3), include_top=False)

x = base_model.output

x = GlobalAveragePooling2D()(x) # chaque imagette : on retient la moyenne

x = Dense(1024, activation='relu')(x) # couche Dense contenant 1024 neurones avec une activation relu // kernel_regularizer=regularizers.l1(0.01)
x = Dense(512, activation='relu')(x)
x = Dropout(rate=0.2)(x)
predictions = Dense(1, activation='sigmoid')(x) # couche Dense avec 1 neurones et une activ sigmoid

earlystop = EarlyStopping(monitor='val_acc', min_delta=0.0001, patience=5, \
                        verbose=1, mode='auto')
callbacks_list = [earlystop]

# this is the model we will train
model = Model(inputs=base_model.input, outputs=predictions) # modele créé qui prend en entrée les entrées et sort les prévisions

# first: train only the top layers (which were randomly initialized)
# i.e. freeze all convolutional InceptionV3 layers
# il faut dire explicitement qu'on ne veut pas réapprendre les poids des couches de convolutions deja apprises
for layer in base_model.layers: # pour cela on fait cette boucle
    layer.trainable = False # il ne fait pas la decente de gradient pour ces paramètres



# compile the model (should be done *after* setting layers to non-trainable)
model.compile(optimizer='rmsprop', loss='binary_crossentropy',metrics=["accuracy"])

# Data
batch_size = 32
datagen = image.ImageDataGenerator(validation_split=.2, # cette version n'existe pas dans notre keras
                                   preprocessing_function=preprocess_input)

#datagen = image.ImageDataGenerator(preprocessing_function=preprocess_input)

train_generator = datagen.flow_from_directory(
    'data_airbus_defi/train',
    target_size=(128, 128), #redimentionnement de l'image
    batch_size=batch_size,
    class_mode='binary', #  sous quelle forme les Y doivent être générés
    shuffle=True,
    subset='training') # ensemble d'apprentissage

validation_generator = datagen.flow_from_directory(
    'data_airbus_defi/train',
    target_size=(128, 128), # meme taille
    batch_size=batch_size,
    class_mode='binary',
    subset='validation')

model.fit_generator(generator=train_generator,
                    steps_per_epoch=train_generator.samples // batch_size,
                    epochs=20,
                    callbacks=callbacks_list,
                    validation_data=validation_generator,
                    validation_steps=validation_generator.samples // batch_size)



model.save('model_ResNet50_2.h5')

/usr/local/lib/python3.6/dist-packages/keras_applications/resnet50.py:265: UserWarning: The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.
  warnings.warn('The output shape of `ResNet50(include_top=False)` '


Found 54575 images belonging to 2 classes.
Found 13643 images belonging to 2 classes.
Epoch 1/20
1705/1705 [==============================] - 221s 130ms/step - loss: 0.4317 - acc: 0.8960 - val_loss: 0.6309 - val_acc: 0.8752
Epoch 2/20
1705/1705 [==============================] - 209s 123ms/step - loss: 0.2152 - acc: 0.9293 - val_loss: 0.8049 - val_acc: 0.8726
Epoch 3/20
1705/1705 [==============================] - 209s 122ms/step - loss: 0.1989 - acc: 0.9338 - val_loss: 0.9378 - val_acc: 0.8846
Epoch 4/20
1705/1705 [==============================] - 208s 122ms/step - loss: 0.1939 - acc: 0.9384 - val_loss: 0.7794 - val_acc: 0.8938
Epoch 5/20
1705/1705 [==============================] - 208s 122ms/step - loss: 0.1865 - acc: 0.9409 - val_loss: 0.8811 - val_acc: 0.8782
Epoch 6/20
1705/1705 [==============================] - 208s 122ms/step - loss: 0.1771 - acc: 0.9443 - val_loss: 0.8674 - val_acc: 0.8796
Epoch 7/20
1705/1705 [==============================] - 207s 122ms/step - loss: 0.1806

In [0]:
# Ensuite je cherche à appliquer mon modele sur les images tests et j'enregistre les résultats dans google drive
# sous la forme qu'il faut pour déposer sur le défi

from keras.preprocessing import image

dico_pred = {}
for im in fichiers:
  img_path = 'data_airbus_defi/test/'+im
  #print(img_path)
  img = image.load_img(img_path, target_size=(128,128))
  x = image.img_to_array(img)
  x = np.expand_dims(x, axis=0)
  x = preprocess_input(x)

  pred = model.predict(x)
  dico_pred[im] = pred

dico_pred2 = {}
for k,v in dico_pred.items():
  v = v.astype(float)[0][0]
  if v >= 0.5 :
    dico_pred2[k] = 1
  else:
    dico_pred2[k] = 0
  



In [0]:
with open("resultats_resNet50_3.csv",'a') as f:
  f.write("name;prediction\n")
  for ele in range(0,17056):
    cle = str(ele)+".jpg"
    f.write(str(cle)+";"+str(dico_pred2[cle])+"\n")
    
!cp 'resultats_resNet50_3.csv' 'drive/My Drive/resultats_resNet50_3.csv'